In [4]:
import pandas as pd

In [1]:
from cassandra.cluster import Cluster


In [20]:
clstr=Cluster()
session=clstr.connect()


In [5]:
data=pd.read_csv('testf.csv')

In [6]:
data

Date/Time      Lat      Lon    Base  prediction
0       8/13/2014 12:50:00  40.7145 -73.9989  B02598           3
1       8/21/2014 15:53:00  40.6900 -74.1782  B02598           2
2        8/13/2014 7:16:00  40.7252 -74.0024  B02598           3
3        8/5/2014 10:42:00  40.7679 -73.9917  B02617           0
4       8/28/2014 20:46:00  40.7515 -73.9755  B02598           0
...                    ...      ...      ...     ...         ...
165850   8/15/2014 7:11:00  40.7428 -73.9966  B02682           3
165851    8/7/2014 6:00:00  40.7441 -73.9913  B02682           3
165852   8/5/2014 18:15:00  40.7597 -73.9682  B02598           0
165853   8/1/2014 16:43:00  40.7522 -73.9718  B02598           0
165854   8/11/2014 9:56:00  40.7192 -73.9630  B02617           6

[165855 rows x 5 columns]

In [7]:
d=[]

In [8]:

from datetime import datetime
for i in data['Date/Time']:
    # Parse the original date string  
    date_object = datetime.strptime(i, "%m/%d/%Y %H:%M:%S")

    # Reformat the date string   
    new_date = date_object.strftime("%Y-%m-%d %H:%M:%S")
    d.append(new_date)

In [9]:
d

['2014-08-13 12:50:00',
 '2014-08-21 15:53:00',
 '2014-08-13 07:16:00',
 '2014-08-05 10:42:00',
 '2014-08-28 20:46:00',
 '2014-08-23 22:18:00',
 '2014-08-12 11:47:00',
 '2014-08-07 07:19:00',
 '2014-08-03 13:32:00',
 '2014-08-07 00:40:00',
 '2014-08-03 03:26:00',
 '2014-08-21 16:42:00',
 '2014-08-03 19:20:00',
 '2014-08-16 17:08:00',
 '2014-08-27 19:18:00',
 '2014-08-20 21:32:00',
 '2014-08-06 20:39:00',
 '2014-08-18 14:10:00',
 '2014-08-25 21:02:00',
 '2014-08-07 14:07:00',
 '2014-08-01 16:38:00',
 '2014-08-14 20:31:00',
 '2014-08-13 04:53:00',
 '2014-08-13 11:21:00',
 '2014-08-08 18:21:00',
 '2014-08-15 13:50:00',
 '2014-08-29 09:24:00',
 '2014-08-02 13:55:00',
 '2014-08-05 18:07:00',
 '2014-08-06 10:26:00',
 '2014-08-01 13:21:00',
 '2014-08-26 10:41:00',
 '2014-08-25 18:02:00',
 '2014-08-11 17:20:00',
 '2014-08-14 01:32:00',
 '2014-08-15 08:09:00',
 '2014-08-05 12:59:00',
 '2014-08-18 19:15:00',
 '2014-08-22 21:28:00',
 '2014-08-28 13:42:00',
 '2014-08-25 06:09:00',
 '2014-08-29 15:

In [10]:
data['Date/Time']=d

In [11]:
data

Date/Time      Lat      Lon    Base  prediction
0       2014-08-13 12:50:00  40.7145 -73.9989  B02598           3
1       2014-08-21 15:53:00  40.6900 -74.1782  B02598           2
2       2014-08-13 07:16:00  40.7252 -74.0024  B02598           3
3       2014-08-05 10:42:00  40.7679 -73.9917  B02617           0
4       2014-08-28 20:46:00  40.7515 -73.9755  B02598           0
...                     ...      ...      ...     ...         ...
165850  2014-08-15 07:11:00  40.7428 -73.9966  B02682           3
165851  2014-08-07 06:00:00  40.7441 -73.9913  B02682           3
165852  2014-08-05 18:15:00  40.7597 -73.9682  B02598           0
165853  2014-08-01 16:43:00  40.7522 -73.9718  B02598           0
165854  2014-08-11 09:56:00  40.7192 -73.9630  B02617           6

[165855 rows x 5 columns]

In [21]:
try:
    session.execute("""
    CREATE KEYSPACE IF NOT EXISTS ath 
    WITH REPLICATION = 
    { 'class' : 'SimpleStrategy', 'replication_factor' : 1 }"""
    )
    session.set_keyspace('ath')
except Exception as e:
    print(e)

In [22]:
create_table_query = """
CREATE TABLE uber (
  id INT,
  base TEXT,
  cluster INT,
  lat FLOAT,
  lon FLOAT,
  time TIMESTAMP,
  cluster_num INT,
  PRIMARY KEY ((cluster), id)
);
"""
try:
    session.execute(create_table_query)
except Exception as e:
    print(e)     

In [44]:
create_table_query = """
CREATE TABLE uberr (
  id INT,
  base TEXT,
  cluster INT,
  lat FLOAT,
  lon FLOAT,
  time TIMESTAMP,
  cluster_num INT,
  PRIMARY KEY ((lat,lon), id)
);
"""
try:
    session.execute(create_table_query)
except Exception as e:
    print(e)     

In [45]:
count=1
for i in data.values:
    session.execute("INSERT INTO uberr (id, time, lat,lon,base,cluster) VALUES (%s, %s,%s, %s,%s,%s)", 
                    (int(count),i[0] , i[1],i[2],i[3],i[4]))
    count=count+1


In [46]:

result = session.execute("SELECT * FROM uberr WHERE id=1 ALLOW FILTERING")
for row in result:
    print(row)


Row(lat=40.714500427246094, lon=-73.9989013671875, id=1, base='B02598', cluster=3, cluster_num=None, time=datetime.datetime(2014, 8, 13, 8, 20))


In [27]:

query='''
SELECT  cluster, COUNT(*)
FROM uber
GROUP BY cluster;''';
result = session.execute(query)
for row in result:
    print(row)


Row(cluster=5, count=12038)
Row(cluster=1, count=5645)
Row(cluster=0, count=55176)
Row(cluster=2, count=1737)
Row(cluster=4, count=480)
Row(cluster=7, count=8769)
Row(cluster=6, count=14155)
Row(cluster=3, count=67855)


In [29]:
result = session.execute("SELECT min(time) FROM uber ")
for row in result:
    print(row)

Row(system_min_time=datetime.datetime(2014, 7, 31, 19, 30))


In [30]:
result = session.execute("SELECT max(time) FROM uber")
for row in result:
    print(row)

Row(system_max_time=datetime.datetime(2014, 8, 31, 19, 29))


In [31]:
from datetime import datetime

date_string = '2014-8-7 19:30'


date_obj = datetime.strptime(date_string, '%Y-%m-%d %H:%M')

formatted_date_string = date_obj.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT * FROM uber WHERE time <= %s ALLOW FILTERING", [formatted_date_string])
for row in result:
    print(row)

Row(cluster=5, id=17, base='B02617', cluster_num=None, lat=40.684600830078125, lon=-73.97769927978516, time=datetime.datetime(2014, 8, 6, 16, 9))
Row(cluster=5, id=121, base='B02617', cluster_num=None, lat=40.677799224853516, lon=-73.9917984008789, time=datetime.datetime(2014, 8, 2, 15, 13))
Row(cluster=5, id=333, base='B02764', cluster_num=None, lat=40.677101135253906, lon=-73.96900177001953, time=datetime.datetime(2014, 8, 6, 16, 37))
Row(cluster=5, id=352, base='B02682', cluster_num=None, lat=40.11149978637695, lon=-74.03399658203125, time=datetime.datetime(2014, 8, 2, 19, 55))
Row(cluster=5, id=491, base='B02598', cluster_num=None, lat=40.60490036010742, lon=-73.98100280761719, time=datetime.datetime(2014, 8, 4, 19, 6))
Row(cluster=5, id=586, base='B02682', cluster_num=None, lat=40.69060134887695, lon=-73.99240112304688, time=datetime.datetime(2014, 8, 4, 3, 0))
Row(cluster=5, id=637, base='B02617', cluster_num=None, lat=40.675498962402344, lon=-73.95819854736328, time=datetime.dat

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Row(cluster=3, id=146953, base='B02617', cluster_num=None, lat=40.75410079956055, lon=-73.99210357666016, time=datetime.datetime(2014, 8, 3, 17, 7))
Row(cluster=3, id=146954, base='B02617', cluster_num=None, lat=40.72639846801758, lon=-74.00199890136719, time=datetime.datetime(2014, 8, 5, 3, 43))
Row(cluster=3, id=146972, base='B02617', cluster_num=None, lat=40.722999572753906, lon=-74.00800323486328, time=datetime.datetime(2014, 8, 7, 7, 50))
Row(cluster=3, id=146992, base='B02682', cluster_num=None, lat=40.745601654052734, lon=-73.9822006225586, time=datetime.datetime(2014, 8, 4, 15, 6))
Row(cluster=3, id=147001, base='B02617', cluster_num=None, lat=40.719398498535156, lon=-73.98690032958984, time=datetime.datetime(2014, 8, 1, 10, 7))
Row(cluster=3, id=147016, base='B02682', cluster_num=None, lat=40.73109817504883, lon=-74.00659942626953, time=datetime.datetime(2014, 8, 5, 19, 34))
Row(cluster=3, id=147021, base='B02682', cluster_num=None, lat=40.71699905395508, lon=-74.0145034790039

In [26]:
from datetime import datetime

date_strating = '2014-8-7 19:30'
date_ending = '2014-8-14 19:30'

date_s = datetime.strptime(date_strating, '%Y-%m-%d %H:%M')
data_e = datetime.strptime(date_ending, '%Y-%m-%d %H:%M')


formatted_date_strating = date_s.strftime('%Y-%m-%dT%H:%M:%SZ')
formatted_date_ending = data_e.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT * FROM uberr WHERE time >= %s AND time <= %s ALLOW FILTERING", [formatted_date_strating, formatted_date_ending])
for row in result:
    print(row)

Row(cluster=5, id=84, base='B02682', cluster_num=None, lat=40.690399169921875, lon=-73.99169921875, time=datetime.datetime(2014, 8, 12, 3, 0))
Row(cluster=5, id=184, base='B02617', cluster_num=None, lat=40.69060134887695, lon=-73.9927978515625, time=datetime.datetime(2014, 8, 9, 0, 50))
Row(cluster=5, id=340, base='B02682', cluster_num=None, lat=40.66350173950195, lon=-73.9811019897461, time=datetime.datetime(2014, 8, 13, 8, 20))
Row(cluster=5, id=452, base='B02617', cluster_num=None, lat=40.69810104370117, lon=-73.97630310058594, time=datetime.datetime(2014, 8, 8, 8, 1))
Row(cluster=5, id=498, base='B02682', cluster_num=None, lat=40.680999755859375, lon=-73.9717025756836, time=datetime.datetime(2014, 8, 12, 16, 2))
Row(cluster=5, id=531, base='B02598', cluster_num=None, lat=40.691898345947266, lon=-74.00070190429688, time=datetime.datetime(2014, 8, 8, 4, 57))
Row(cluster=5, id=546, base='B02598', cluster_num=None, lat=40.68479919433594, lon=-73.99490356445312, time=datetime.datetime(2

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [33]:
from datetime import datetime

date_strating = '2014-8-14 19:30'
date_ending = '2014-8-21 19:30'

date_s = datetime.strptime(date_strating, '%Y-%m-%d %H:%M')
data_e = datetime.strptime(date_ending, '%Y-%m-%d %H:%M')

2
formatted_date_strating = date_s.strftime('%Y-%m-%dT%H:%M:%SZ')
formatted_date_ending = data_e.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT * FROM uber WHERE time >= %s AND time <= %s ALLOW FILTERING", [formatted_date_strating, formatted_date_ending])
for row in result:
    print(row)

Row(cluster=5, id=147, base='B02598', cluster_num=None, lat=40.68370056152344, lon=-73.97640228271484, time=datetime.datetime(2014, 8, 21, 17, 29))
Row(cluster=5, id=231, base='B02617', cluster_num=None, lat=40.57529830932617, lon=-73.98390197753906, time=datetime.datetime(2014, 8, 20, 10, 26))
Row(cluster=5, id=238, base='B02682', cluster_num=None, lat=40.6172981262207, lon=-74.03209686279297, time=datetime.datetime(2014, 8, 15, 15, 8))
Row(cluster=5, id=304, base='B02617', cluster_num=None, lat=40.674198150634766, lon=-73.97270202636719, time=datetime.datetime(2014, 8, 20, 18, 22))
Row(cluster=5, id=342, base='B02617', cluster_num=None, lat=40.667198181152344, lon=-73.9927978515625, time=datetime.datetime(2014, 8, 15, 14, 43))
Row(cluster=5, id=363, base='B02682', cluster_num=None, lat=40.666500091552734, lon=-73.97740173339844, time=datetime.datetime(2014, 8, 15, 19, 37))
Row(cluster=5, id=503, base='B02512', cluster_num=None, lat=40.67129898071289, lon=-73.96260070800781, time=date

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
from datetime import datetime

date_strating = '2014-8-21 19:30'
date_ending = '2014-8-28 19:30'

date_s = datetime.strptime(date_strating, '%Y-%m-%d %H:%M')
data_e = datetime.strptime(date_ending, '%Y-%m-%d %H:%M')


formatted_date_strating = date_s.strftime('%Y-%m-%dT%H:%M:%SZ')
formatted_date_ending = data_e.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT * FROM uber WHERE time >= %s AND time <= %s ALLOW FILTERING", [formatted_date_strating, formatted_date_ending])
for row in result:
    print(row)

In [36]:
from datetime import datetime

date_string = '2014-8-28 19:30'


date_obj = datetime.strptime(date_string, '%Y-%m-%d %H:%M')

formatted_date_string = date_obj.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT * FROM uber WHERE time >= %s ALLOW FILTERING", [formatted_date_string])
for row in result:
    print(row)

Row(cluster=5, id=156, base='B02617', cluster_num=None, lat=40.68170166015625, lon=-73.95850372314453, time=datetime.datetime(2014, 8, 29, 11, 26))
Row(cluster=5, id=343, base='B02617', cluster_num=None, lat=40.687198638916016, lon=-73.9834976196289, time=datetime.datetime(2014, 8, 30, 1, 28))
Row(cluster=5, id=450, base='B02617', cluster_num=None, lat=40.61640167236328, lon=-74.09359741210938, time=datetime.datetime(2014, 8, 30, 15, 32))
Row(cluster=5, id=898, base='B02617', cluster_num=None, lat=40.688201904296875, lon=-73.97869873046875, time=datetime.datetime(2014, 8, 29, 1, 27))
Row(cluster=5, id=909, base='B02617', cluster_num=None, lat=40.62009811401367, lon=-73.92890167236328, time=datetime.datetime(2014, 8, 29, 2, 46))
Row(cluster=5, id=916, base='B02617', cluster_num=None, lat=40.6708984375, lon=-73.95819854736328, time=datetime.datetime(2014, 8, 31, 7, 30))
Row(cluster=5, id=937, base='B02682', cluster_num=None, lat=40.55860137939453, lon=-73.90149688720703, time=datetime.da

Row(cluster=3, id=19985, base='B02682', cluster_num=None, lat=40.74720001220703, lon=-73.9894027709961, time=datetime.datetime(2014, 8, 30, 2, 46))
Row(cluster=3, id=19998, base='B02617', cluster_num=None, lat=40.72010040283203, lon=-74.01020050048828, time=datetime.datetime(2014, 8, 29, 13, 3))
Row(cluster=3, id=20016, base='B02617', cluster_num=None, lat=40.73749923706055, lon=-73.98400115966797, time=datetime.datetime(2014, 8, 29, 17, 58))
Row(cluster=3, id=20021, base='B02682', cluster_num=None, lat=40.72639846801758, lon=-74.00569915771484, time=datetime.datetime(2014, 8, 30, 11, 3))
Row(cluster=3, id=20080, base='B02617', cluster_num=None, lat=40.747398376464844, lon=-73.98780059814453, time=datetime.datetime(2014, 8, 30, 21, 43))
Row(cluster=3, id=20114, base='B02617', cluster_num=None, lat=40.73509979248047, lon=-73.98280334472656, time=datetime.datetime(2014, 8, 30, 12, 13))
Row(cluster=3, id=20135, base='B02617', cluster_num=None, lat=40.70800018310547, lon=-74.01139831542969

In [34]:
from datetime import datetime

date_string = '2014-8-7 19:30'


date_obj = datetime.strptime(date_string, '%Y-%m-%d %H:%M')

formatted_date_string = date_obj.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT cluster, COUNT(*) AS count FROM uber WHERE time < %s GROUP BY cluster  ALLOW FILTERING;", [formatted_date_string])


In [35]:
for row in result:
    x=0
    if x< row.count:
        x=row.count
        y=row.cluster
print(y,':',x)

3 : 16613


In [41]:
from datetime import datetime

date_strating = '2014-8-7 19:30'
date_ending = '2014-8-14 19:30'

date_s = datetime.strptime(date_strating, '%Y-%m-%d %H:%M')
data_e = datetime.strptime(date_ending, '%Y-%m-%d %H:%M')


formatted_date_strating = date_s.strftime('%Y-%m-%dT%H:%M:%SZ')
formatted_date_ending = data_e.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT cluster, COUNT(*) AS count FROM uber WHERE time >= %s AND time <= %s GROUP BY cluster ALLOW FILTERING", [formatted_date_strating, formatted_date_ending])
for row in result:
    x=0
    if x< row.count:
        x=row.count
        y=row.cluster
print(y,':',x)

3 : 15797


In [42]:
from datetime import datetime

date_strating = '2014-8-14 19:30'
date_ending = '2014-8-21 19:30'

date_s = datetime.strptime(date_strating, '%Y-%m-%d %H:%M')
data_e = datetime.strptime(date_ending, '%Y-%m-%d %H:%M')


formatted_date_strating = date_s.strftime('%Y-%m-%dT%H:%M:%SZ')
formatted_date_ending = data_e.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT cluster, COUNT(*) AS count FROM uber WHERE time >= %s AND time <= %s GROUP BY cluster ALLOW FILTERING", [formatted_date_strating, formatted_date_ending])
for row in result:
    x=0
    if x< row.count:
        x=row.count
        y=row.cluster
print(y,':',x)

3 : 15153


In [43]:
from datetime import datetime

date_strating = '2014-8-21 19:30'
date_ending = '2014-8-28 19:30'

date_s = datetime.strptime(date_strating, '%Y-%m-%d %H:%M')
data_e = datetime.strptime(date_ending, '%Y-%m-%d %H:%M')


formatted_date_strating = date_s.strftime('%Y-%m-%dT%H:%M:%SZ')
formatted_date_ending = data_e.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT cluster, COUNT(*) AS count FROM uber WHERE time >= %s AND time <= %s GROUP BY cluster ALLOW FILTERING", [formatted_date_strating, formatted_date_ending])
for row in result:
    x=0
    if x< row.count:
        x=row.count
        y=row.cluster
print(y,':',x)

3 : 14579


In [125]:
from datetime import datetime

date_string = '2014-8-10 19:30'


date_obj = datetime.strptime(date_string, '%Y-%m-%d %H:%M')

formatted_date_string = date_obj.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT lat,lon, COUNT(*) AS count FROM uberr WHERE time < %s GROUP BY lat,lon  ALLOW FILTERING;", [formatted_date_string])


In [126]:
count=0
lat=0
lon=0
for i in result:
    if count < i.count:
        count=i.count
        lat=i.lat
        lon=i.lon
print('max number:',count,'(lat,lon)=','(',lat,',',lon,')')
        

max number: 38 (lat,lon)= ( 40.64469909667969 , -73.78209686279297 )


In [47]:
from datetime import datetime

date_strating = '2014-8-10 19:30'
date_ending = '2014-8-20 19:30'

date_s = datetime.strptime(date_strating, '%Y-%m-%d %H:%M')
data_e = datetime.strptime(date_ending, '%Y-%m-%d %H:%M')


formatted_date_strating = date_s.strftime('%Y-%m-%dT%H:%M:%SZ')
formatted_date_ending = data_e.strftime('%Y-%m-%dT%H:%M:%SZ')

result = session.execute("SELECT lat,lon, COUNT(*) AS count FROM uberr WHERE time >= %s AND time <= %s GROUP BY lat,lon  ALLOW FILTERING", [formatted_date_strating, formatted_date_ending])
count=0
lat=0
lon=0
for i in result:
    if count < i.count:
        count=i.count
        lat=i.lat
        lon=i.lon
print('max number:',count,'(lat,lon)=','(',lat,',',lon,')')
        

max number: 53 (lat,lon)= ( 40.644798278808594 , -73.78199768066406 )


In [17]:

session.execute("DROP KEYSPACE ath")
clstr.shutdown()

In [18]:

clstr.shutdown()